# Eat Safe, Love

## Part 1: Database and Jupyter Notebook Set Up

Import the data provided in the `establishments.json` file from your Terminal. Name the database `uk_food` and the collection `establishments`.

Within this markdown cell, copy the line of text you used to import the data from your Terminal. This way, future analysts will be able to repeat your process.

e.g.: Import the dataset with `YOUR IMPORT TEXT HERE`

In [9]:
!mongoimport --type json -d uk_food -c establishments --drop --jsonArray Resources/establishments.json

2024-02-08T13:01:21.926-0600	connected to: mongodb://localhost/
2024-02-08T13:01:21.926-0600	dropping: uk_food.establishments
2024-02-08T13:01:24.070-0600	39779 document(s) imported successfully. 0 document(s) failed to import.


In [10]:
# Import dependencies
from pymongo import MongoClient
from pprint import pprint

In [11]:
# Create an instance of MongoClient
mongo = MongoClient(port=27017)

In [12]:
# confirm that our new database was created
print(mongo.list_database_names())

['admin', 'autosaurus', 'classDB', 'config', 'epa', 'gardenDB', 'local', 'met', 'petsitly_marketing', 'travel_db', 'uk_food']


In [13]:
# assign the uk_food database to a variable name
db = mongo['uk_food']

In [14]:
# review the collections in our new database
print(db.list_collection_names())

['establishments']


In [15]:
# review a document in the establishments collection
pprint(db['establishments'].find_one())

{'AddressLine1': '1 The Droveway',
 'AddressLine2': 'St Margarets Bay',
 'AddressLine3': 'Kent',
 'AddressLine4': '',
 'BusinessName': 'FirstLight Bar & Café',
 'BusinessType': 'Restaurant/Cafe/Canteen',
 'BusinessTypeID': 1,
 'ChangesByServerID': 0,
 'Distance': 4587.64041272672,
 'FHRSID': 1290215,
 'LocalAuthorityBusinessID': 'PI/000083029',
 'LocalAuthorityCode': '182',
 'LocalAuthorityEmailAddress': 'publicprotection@dover.gov.uk',
 'LocalAuthorityName': 'Dover',
 'LocalAuthorityWebSite': 'http://www.dover.gov.uk/',
 'NewRatingPending': False,
 'Phone': '',
 'PostCode': 'CT15 6DH',
 'RatingDate': '2020-11-09T00:00:00',
 'RatingKey': 'fhrs_5_en-gb',
 'RatingValue': '5',
 'RightToReply': '',
 'SchemeType': 'FHRS',
 '_id': ObjectId('65c525016327a0bf396fb6ee'),
 'geocode': {'latitude': '51.150625', 'longitude': '1.378231'},
 'links': [{'href': 'https://api.ratings.food.gov.uk/establishments/1290215',
            'rel': 'self'}],
 'meta': {'dataSource': None,
          'extractDate': '

In [16]:
# assign the collection to a variable
establishments = db['establishments']

## Part 2: Update the Database

1. An exciting new halal restaurant just opened in Greenwich, but hasn't been rated yet. The magazine has asked you to include it in your analysis. Add the following restaurant "Penang Flavours" to the database.

In [17]:
# Create a dictionary for the new restaurant data
penang_flavours = {
    'BusinessName': 'Penang Flavours'
} 


InsertOneResult(ObjectId('65c527b9a40d3e96840634a6'), acknowledged=True)

In [ ]:
# Insert the new restaurant into the collection
establishments.insert_one(penang_flavours)

In [19]:
# Check that the new restaurant was inserted
query = {'BusinessName' : 'Penang Flavours'}
pprint(list(establishments.find(query)))

[{'BusinessName': 'Penang Flavours',
  '_id': ObjectId('65c527b9a40d3e96840634a6')}]


2. Find the BusinessTypeID for "Restaurant/Cafe/Canteen" and return only the `BusinessTypeID` and `BusinessType` fields.

In [22]:
# Find the BusinessTypeID for "Restaurant/Cafe/Canteen" and return only the BusinessTypeID and BusinessType fields
query = {'BusinessType' : {'$regex': "Restaurant/Cafe/Canteen"}}
fields = {'BusinessTypeID' : 1, "BusinessType" : 1}
result = establishments.find(query,fields)

pprint(list(result))

[{'BusinessType': 'Restaurant/Cafe/Canteen',
  'BusinessTypeID': 1,
  '_id': ObjectId('65c525016327a0bf396fb6ee')},
 {'BusinessType': 'Restaurant/Cafe/Canteen',
  'BusinessTypeID': 1,
  '_id': ObjectId('65c525016327a0bf396fb6ef')},
 {'BusinessType': 'Restaurant/Cafe/Canteen',
  'BusinessTypeID': 1,
  '_id': ObjectId('65c525016327a0bf396fb6f0')},
 {'BusinessType': 'Restaurant/Cafe/Canteen',
  'BusinessTypeID': 1,
  '_id': ObjectId('65c525016327a0bf396fb6f2')},
 {'BusinessType': 'Restaurant/Cafe/Canteen',
  'BusinessTypeID': 1,
  '_id': ObjectId('65c525016327a0bf396fb6f3')},
 {'BusinessType': 'Restaurant/Cafe/Canteen',
  'BusinessTypeID': 1,
  '_id': ObjectId('65c525016327a0bf396fb6f4')},
 {'BusinessType': 'Restaurant/Cafe/Canteen',
  'BusinessTypeID': 1,
  '_id': ObjectId('65c525016327a0bf396fb6f9')},
 {'BusinessType': 'Restaurant/Cafe/Canteen',
  'BusinessTypeID': 1,
  '_id': ObjectId('65c525016327a0bf396fb6fa')},
 {'BusinessType': 'Restaurant/Cafe/Canteen',
  'BusinessTypeID': 1,
  '_

3. Update the new restaurant with the `BusinessTypeID` you found.

In [23]:
# Update the new restaurant with the correct BusinessTypeID
establishments.update_one(
    {'BusinessName': 'Penang Flavours'},
    {'$push':
        {'BusinessTypeID': 1},
        # {'BusinessType' : 'Restaurant/Cafe/Canteen'}
     }


)

UpdateResult({'n': 1, 'nModified': 1, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)

In [24]:
# Confirm that the new restaurant was updated
query = {'BusinessName' : 'Penang Flavours'}
pprint(list(establishments.find(query)))

[{'BusinessName': 'Penang Flavours',
  'BusinessTypeID': [1],
  '_id': ObjectId('65c527b9a40d3e96840634a6')}]


4. The magazine is not interested in any establishments in Dover, so check how many documents contain the Dover Local Authority. Then, remove any establishments within the Dover Local Authority from the database, and check the number of documents to ensure they were deleted.

In [25]:
# Find how many documents have LocalAuthorityName as "Dover"
query = {'LocalAuthorityName' : 'Dover'}
dover = establishments.find(query)
pprint(list(dover))

[{'AddressLine1': '1 The Droveway',
  'AddressLine2': 'St Margarets Bay',
  'AddressLine3': 'Kent',
  'AddressLine4': '',
  'BusinessName': 'FirstLight Bar & Café',
  'BusinessType': 'Restaurant/Cafe/Canteen',
  'BusinessTypeID': 1,
  'ChangesByServerID': 0,
  'Distance': 4587.64041272672,
  'FHRSID': 1290215,
  'LocalAuthorityBusinessID': 'PI/000083029',
  'LocalAuthorityCode': '182',
  'LocalAuthorityEmailAddress': 'publicprotection@dover.gov.uk',
  'LocalAuthorityName': 'Dover',
  'LocalAuthorityWebSite': 'http://www.dover.gov.uk/',
  'NewRatingPending': False,
  'Phone': '',
  'PostCode': 'CT15 6DH',
  'RatingDate': '2020-11-09T00:00:00',
  'RatingKey': 'fhrs_5_en-gb',
  'RatingValue': '5',
  'RightToReply': '',
  'SchemeType': 'FHRS',
  '_id': ObjectId('65c525016327a0bf396fb6ee'),
  'geocode': {'latitude': '51.150625', 'longitude': '1.378231'},
  'links': [{'href': 'https://api.ratings.food.gov.uk/establishments/1290215',
             'rel': 'self'}],
  'meta': {'dataSource': None

In [27]:
# Delete all documents where LocalAuthorityName is "Dover"
establishments.delete_many(
            {'LocalAuthorityName' : 'Dover'})



DeleteResult({'n': 0, 'ok': 1.0}, acknowledged=True)

In [28]:
# Check if any remaining documents include Dover
query = {'LocalAuthorityName' : 'Dover'}
dover = establishments.find(query)
pprint(list(dover))

[]


In [29]:
# Check that other documents remain with 'find_one'
establishments.find_one()

{'_id': ObjectId('65c525016327a0bf396fb9d2'),
 'FHRSID': 647177,
 'ChangesByServerID': 0,
 'LocalAuthorityBusinessID': 'PI/000041489',
 'BusinessName': 'Wear Bay Bowls Club',
 'BusinessType': 'Pub/bar/nightclub',
 'BusinessTypeID': 7843,
 'AddressLine1': 'Wear Bay Road',
 'AddressLine2': 'Folkestone',
 'AddressLine3': 'Kent',
 'AddressLine4': '',
 'PostCode': 'CT19 6PY',
 'Phone': '',
 'RatingValue': '4',
 'RatingKey': 'fhrs_4_en-gb',
 'RatingDate': '2014-03-31T00:00:00',
 'LocalAuthorityCode': '188',
 'LocalAuthorityName': 'Folkestone and Hythe',
 'LocalAuthorityWebSite': 'http://www.folkestone-hythe.gov.uk',
 'LocalAuthorityEmailAddress': 'foodteam@folkestone-hythe.gov.uk',
 'scores': {'Hygiene': 5, 'Structural': 5, 'ConfidenceInManagement': 10},
 'SchemeType': 'FHRS',
 'geocode': {'longitude': '1.196408', 'latitude': '51.086058'},
 'RightToReply': '',
 'Distance': 4591.821311183521,
 'NewRatingPending': False,
 'meta': {'dataSource': None,
  'extractDate': '0001-01-01T00:00:00',
  '

5. Some of the number values are stored as strings, when they should be stored as numbers.

Use `update_many` to convert `latitude` and `longitude` to decimal numbers.

In [40]:
query = {'BusinessType' : {'$regex': "Restaurant/Cafe/Canteen"}}
fields = {'BusinessTypeID' : 1, "BusinessType" : 1, 'geocode.latitude' : 1, 'geocode.longitude' : 1, 'RatingValue': 1}
result = establishments.find(query,fields)
pprint(list(result))

[{'BusinessType': 'Restaurant/Cafe/Canteen',
  'BusinessTypeID': 1,
  'RatingValue': '5',
  '_id': ObjectId('65c525016327a0bf396fb9dd'),
  'geocode': {'latitude': Decimal128('51.0783519967076'),
              'longitude': Decimal128('1.18590330311705')}},
 {'BusinessType': 'Restaurant/Cafe/Canteen',
  'BusinessTypeID': 1,
  'RatingValue': '4',
  '_id': ObjectId('65c525016327a0bf396fb9e2'),
  'geocode': {'latitude': Decimal128('51.0783519967076'),
              'longitude': Decimal128('1.18590330311705')}},
 {'BusinessType': 'Restaurant/Cafe/Canteen',
  'BusinessTypeID': 1,
  'RatingValue': '5',
  '_id': ObjectId('65c525016327a0bf396fb9e7'),
  'geocode': {'latitude': Decimal128('51.083812'),
              'longitude': Decimal128('1.195625')}},
 {'BusinessType': 'Restaurant/Cafe/Canteen',
  'BusinessTypeID': 1,
  'RatingValue': '3',
  '_id': ObjectId('65c525016327a0bf396fb9f0'),
  'geocode': {'latitude': Decimal128('51.0783519967076'),
              'longitude': Decimal128('1.18590330311

In [38]:
# Change the data type from String to Decimal for longitude and latitude
establishments.update_many({}, 
                           [{'$set' : {'geocode.latitude' :{'$toDecimal': '$geocode.latitude'},
                                        'geocode.longitude' :{'$toDecimal': '$geocode.longitude'}}}])

UpdateResult({'n': 38786, 'nModified': 38786, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)

Use `update_many` to convert `RatingValue` to integer numbers.

In [39]:
# Set non 1-5 Rating Values to Null
non_ratings = ["AwaitingInspection", "Awaiting Inspection", "AwaitingPublication", "Pass", "Exempt"]
establishments.update_many({"RatingValue": {"$in": non_ratings}}, [ {'$set':{ "RatingValue" : None}} ])

UpdateResult({'n': 4091, 'nModified': 4091, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)

In [46]:
# Change the data type from String to Integer for RatingValue
establishments.update_many(
    {}, 
    [{'$set': {'RatingValue': {'$toInt': '$RatingValue'}}}]
)


UpdateResult({'n': 38786, 'nModified': 0, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)

In [45]:
# Check that the coordinates and rating value are now numbers
query = {'BusinessType' : {'$regex': "Restaurant/Cafe/Canteen"}}
fields = {'geocode.latitude' : 1, 'geocode.longitude' : 1, 'RatingValue': 1}
result = establishments.find(query,fields)
pprint(list(result))

[{'RatingValue': 5,
  '_id': ObjectId('65c525016327a0bf396fb9dd'),
  'geocode': {'latitude': Decimal128('51.0783519967076'),
              'longitude': Decimal128('1.18590330311705')}},
 {'RatingValue': 4,
  '_id': ObjectId('65c525016327a0bf396fb9e2'),
  'geocode': {'latitude': Decimal128('51.0783519967076'),
              'longitude': Decimal128('1.18590330311705')}},
 {'RatingValue': 5,
  '_id': ObjectId('65c525016327a0bf396fb9e7'),
  'geocode': {'latitude': Decimal128('51.083812'),
              'longitude': Decimal128('1.195625')}},
 {'RatingValue': 3,
  '_id': ObjectId('65c525016327a0bf396fb9f0'),
  'geocode': {'latitude': Decimal128('51.0783519967076'),
              'longitude': Decimal128('1.18590330311705')}},
 {'RatingValue': 4,
  '_id': ObjectId('65c525016327a0bf396fb9f1'),
  'geocode': {'latitude': Decimal128('51.0783519967076'),
              'longitude': Decimal128('1.18590330311705')}},
 {'RatingValue': 5,
  '_id': ObjectId('65c525016327a0bf396fb9f8'),
  'geocode': {'lat